**Note: Please create a local copy of this notebook on your Google account before using it**

# *Data Science for Energy and Buildings*

### *The case of the German Electricity Market*

Authors: Tim Diller and Gregor Henze

Created: June 28, 2023


First, mount your Google Drive to the Colab instance.
This needs to be a two step process, as the mount() function does not accept folder names with a Space in it, but GDrive dictates that the root folder is called 'My Drive'.

You only need to run this block once. An if clause checks if you are already in the right directory, and only moves directory if it is still required.

Please download the Energy_df.pkl file that can be found under "data/German energy grid/", and add it to your GDrive.
Then specify the location of the file in the pickle_file_path variable in the block below

In [ ]:
from google.colab import drive  # The google colab module to access folders on GDrive
import os  # the python module for all things related to the OS.

drive.mount('/content/drive')  # we mount our gDrive drive at the startpoint

# next we check if we are already in the right folder, and navigate there if we are not
current_directory = os.getcwd()
parent_directory = os.path.dirname(current_directory)
os.path.basename(parent_directory)
# replace this with the path to the folder where you stored the Energy_df.pkl (also in this github folder)
pickle_file_path = "drive/My Drive/ADAM/Energy_Market/data/power_grid_germany"

if os.path.basename(current_directory) == 'power_grid_germany' and os.path.basename(parent_directory) == 'data':
    print('you are already in the right folder, no need to run this twice')
else:

    try:  # we see if we can navigate to the folder
        os.chdir(pickle_file_path)

    except FileNotFoundError:  # and handle it if it goes wrong
        print('something else went wrong, probably you did not add a link to your ADAM folder in the top level of your gDrive')
        raise


# commands start start with '!' indicate console commands)
print('this folder contains the following files: ')
!ls  # this command lists the content of the current folder


# make sure we are in the right directory
print('current directory'+ os.getcwd())


Mounted at /content/drive
this folder contains the following files: 
energy-charts_Electricity_production_and_spot_prices_in_Germany_in_2020.csv
energy-charts_Public_net_electricity_generation_in_Germany_in_2020.csv
energy-charts_spot_prices_in_Germany_in_2020.csv
Energy_df.pkl
current directory/content/drive/.shortcut-targets-by-id/1G-VhmOWPi9pCf6dIRFXcobLOaAHN-j8_/ADAM/Energy_Market/data/power_grid_germany


First we **import** the required libraries
For understanding what happens when we **import** a library, ask your favourite LLM, like was done [here](https://chat.openai.com/share/ac69ef94-4972-4b60-88f5-2b98c9eeb067).



Pandas is the go-to library for handling DataFrames, see [here](https://pandas.pydata.org/docs/).

Numpy (NumericalPython) is for efficiently handling large matrix operations, see [here](https://numpy.org/doc/).

Plotly is our primary plotting library for this course, enabling a wide range of plots, see [here](https://numpy.org/doc/).

In [ ]:

import pandas as pd  # pandas is the main data handling package in python
import numpy as np  # NumericalPython is the main package for mathematical/Matrix operations in python
import calendar  # calendar package for turning month numbers into names
import pickle  # pickle is a package for 'pickling' objects, saving them in their original shape
import scipy.stats as stats  # scipy is a package for many different scientific computing procedures
from IPython.display import display  # display is a package to facilitate viewing of tables and other structures
import random  # random is used to draw random samples, generate random numbers, etc.
from scipy.interpolate import griddata  # is used to turn array values into grids

# we import a range of different packages from the plotly library
import plotly.express as px  # plotly.express is used to quickly make nice simple plots
import plotly.graph_objects as go  # for more complex plots, we need graph_objects
import plotly.subplots as sp
from plotly.subplots import make_subplots  # for plotting multiple plots in one figure

# this is to render the plots correctly when inside colab
import plotly.io as pio
pio.renderers.default = 'colab'

# required for saving plots in colab
!pip install -U kaleido



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 12.4 MB/s eta 0:00:00


# Loading and viewing the contents of the Datafile

We use pandas (and its builtin pickle functionality) to read the pickle that we created in chapter 0

Pickle is a very useful package for 'pickling' python objects like functions, classes, DataFrames. It preserves all structures and informations from the original datatype, making it a very convenient format to store processed data. For documentation, see [here](https://docs.python.org/3/library/pickle.html).




In [ ]:
data_df = pd.read_pickle('Energy_df.pkl')  # pandas (the pd) has the pickle functionality built in.

In [ ]:
# df.head() is a useful function to get a quick overview over the content of a DataFrame
data_df.head()


Date (GMT+1)  Day Ahead Auction  Import Balance  Nuclear  \
1  2020-01-01 00:00:00+01:00              41.88           834.9   8095.9   
2  2020-01-01 01:00:00+01:00              38.60          1021.5   8090.7   
3  2020-01-01 02:00:00+01:00              36.55          1527.9   8094.5   
4  2020-01-01 03:00:00+01:00              32.32           642.1   8081.4   
5  2020-01-01 04:00:00+01:00              30.85           527.7   8075.8   

   Hydro Run-of-River  Biomass  Fossil brown coal / lignite  Fossil hard coal  \
1              1591.9   5149.5                       9203.9            2104.9   
2              1581.7   5126.3                       9331.5            2052.5   
3              1578.8   5127.9                       9377.4            1902.5   
4              1565.4   5120.0                       9414.5            2010.8   
5              1561.9   5118.3                       9468.3            2023.4   

   Fossil oil  Fossil gas  ...  Hydro water reservoir  Hydro pumped storage  \
1       101.1      5525.4  ...                   53.6                 605.7   
2       101.1      4991.5  ...                   64.4                 369.8   
3       101.4      4750.5  ...                  108.7                1409.9   
4       101.1      4773.0  ...                  134.9                1408.3   
5       101.1      4672.5  ...                   59.8                1279.5   

   Others   Waste  Wind offshore  Wind onshore  Solar     Load  hour_of_day  \
1    82.0  1399.9          501.3        5884.0    0.0  43856.9            0   
2    80.9  1385.0          890.6        6062.7    0.0  43023.9            1   
3    79.7  1349.4         1534.6        5770.2    0.0  41971.3            2   
4    81.1  1343.9         1902.9        5497.4    0.0  40723.8            3   
5    81.2  1380.9         2252.9        5469.3    0.0  40407.3            4   

   month  
1      1  
2      1  
3      1  
4      1  
5      1  

[5 rows x 21 columns]

To print all columns that this dataframe contains, we can call the df.columns property of the DataFrame

In [ ]:
# we can also print the list of columns that the dataframe contains:
print(data_df.columns)

Index(['Date (GMT+1)', 'Day Ahead Auction', 'Import Balance', 'Nuclear',
       'Hydro Run-of-River', 'Biomass', 'Fossil brown coal / lignite',
       'Fossil hard coal', 'Fossil oil', 'Fossil gas', 'Geothermal',
       'Hydro water reservoir', 'Hydro pumped storage', 'Others', 'Waste',
       'Wind offshore', 'Wind onshore', 'Solar', 'Load', 'hour_of_day',
       'month'],
      dtype='object')


We now manually define the subset of the table that contains all the power sources


In [ ]:
# this is a subset of coloumns of our data_df, comprising all the columns representing power sources
power_sources = ['Nuclear', 'Hydro Run-of-River', 'Biomass', 'Fossil brown coal / lignite', 'Fossil hard coal',
                 'Fossil oil', 'Fossil gas', 'Geothermal', 'Hydro water reservoir', 'Hydro pumped storage',
                 'Others', 'Waste', 'Wind offshore', 'Wind onshore', 'Solar',]  #  'Import Balance']

# and this is the subset that defines renewable energy sources
renewable_sources = ['Hydro Run-of-River', 'Biomass', 'Geothermal', 'Hydro water reservoir', 'Hydro pumped storage',
                 'Others', 'Waste', 'Wind offshore', 'Wind onshore', 'Solar',]

# for plotting annotation, it will be useful to map the month numbers to their respective names:
month_number_to_name = {
    1: 'January',
    2: 'February',
    3: 'March',
    4: 'April',
    5: 'May',
    6: 'June',
    7: 'July',
    8: 'August',
    9: 'September',
    10: 'October',
    11: 'November',
    12: 'December'
}


Next we want to generate a table of summary statistics (median, mean, percentiles, standard deviation, ...) of our data:
[LLM Link](https://chat.openai.com/share/64b20909-2e05-42af-9e1c-d226a50e4a74):

In [ ]:
# Initialize an empty list to store summary statistics DataFrames
summary_dfs = []
# Calculate summary statistics for each power source column
for column in power_sources:
    mean_val = int(data_df[column].mean().round(0))
    median_val = int(data_df[column].median().round(0))
    q10_val = int(data_df[column].quantile(0.10).round(0))
    q25_val = int(data_df[column].quantile(0.25).round(0))
    q75_val = int(data_df[column].quantile(0.75).round(0))
    q90_val = int(data_df[column].quantile(0.90).round(0))
    min_val = data_df[column].min()
    max_val = data_df[column].max()
    std_val = data_df[column].std().round(2)

    # Create a DataFrame for the current power source column's summary statistics
    summary_df = pd.DataFrame({'Column': [column],
                               'Mean': [mean_val],
                               'Median': [median_val],
                               'Quantile 10%': [q10_val],
                               'Quantile 25%': [q25_val],
                               'Quantile 75%': [q75_val],
                               'Quantile 90%': [q90_val],
                               'Min': [min_val],
                               'Max': [max_val],
                               'Standard Deviation': [std_val]})

    # Append the summary DataFrame to the list
    summary_dfs.append(summary_df)

# Concatenate all the summary statistics DataFrames into one
summary_df = pd.concat(summary_dfs, ignore_index=True)

# Display the summary DataFrame as a graphical object
display(summary_df)
# note that display() leads to a much cleaner output than just calling print(summary_df)
print(summary_df)


Column   Mean  Median  Quantile 10%  Quantile 25%  \
0                       Nuclear   6934    6801          5285          6452   
1            Hydro Run-of-River   1973    2008          1549          1698   
2                       Biomass   4865    4875          4567          4696   
3   Fossil brown coal / lignite   9347    9694          4084          5963   
4              Fossil hard coal   4035    2689          1406          1846   
5                    Fossil oil     74      71            46            60   
6                    Fossil gas   6492    6348          2950          4365   
7                    Geothermal     20      20            14            16   
8         Hydro water reservoir    148     123            41            70   
9          Hydro pumped storage    773     704           160           331   
10                       Others     82      80            69            75   
11                        Waste   1140    1203           770          1060   
12                Wind offshore   3062    3047           404          1139   
13                 Wind onshore  11693    9110          2084          4180   
14                        Solar   5531     100             0             0   

    Quantile 75%  Quantile 90%     Min      Max  Standard Deviation  
0           7831          8024  3758.4   8180.9              969.38  
1           2205          2377  1288.4   2707.1              309.39  
2           5033          5148  4172.2   5378.5              218.56  
3          12364         14688  2809.6  16663.0             3753.12  
4           4946          9059   671.4  17381.6             3300.02  
5             95           102    42.4    234.7               23.45  
6           7982         10567  1177.1  15745.8             2856.61  
7             23            25     8.4     27.6                4.11  
8            204           299     4.2    608.2              101.54  
9           1147          1423     0.3   3204.4              516.75  
10            89            98    30.3    120.7               12.33  
11          1319          1383   206.4   1537.9              247.41  
12          4954          5751     0.0   6983.8             2004.83  
13         17026         26142    91.1  40374.5             9212.07  
14          9006         19585     0.0  35190.2             8441.56

                         Column   Mean  Median  Quantile 10%  Quantile 25%  \
0                       Nuclear   6934    6801          5285          6452   
1            Hydro Run-of-River   1973    2008          1549          1698   
2                       Biomass   4865    4875          4567          4696   
3   Fossil brown coal / lignite   9347    9694          4084          5963   
4              Fossil hard coal   4035    2689          1406          1846   
5                    Fossil oil     74      71            46            60   
6                    Fossil gas   6492    6348          2950          4365   
7                    Geothermal     20      20            14            16   
8         Hydro water reservoir    148     123            41            70   
9          Hydro pumped storage    773     704           160           331   
10                       Others     82      80            69            75   
11                        Waste   1140    1203           770    

# Data verification

We need to check whether the data is probable and realiable. So we can run a range of checks to check for outliers or improbable data.

One verification is to check how well the power production fits the load on the system. For this, we calculate the energy balance for each line in the data frame. This can then be shown as a violin plot. [Ask your LLM how:](https://chat.openai.com/share/33ff2634-70e6-4156-80db-70c81372ad0e)



In [ ]:
# we write a function that calculates the energy balance
def calculate_energy_balance(row):
    power_production_sum = sum(row[column] for column in power_sources)
    energy_balance = power_production_sum - row['Load']
    return energy_balance

# we use df.apply() to create the new column
data_df['Energy_Balance'] = data_df.apply(calculate_energy_balance, axis=1)


now we can use this column to create the violin plot

In [ ]:
fig = px.violin(data_df, y='Energy_Balance', box=True, points="all", title='Energy Balance Violin Plot')

# Show the plot
fig.show()

We see there is a large discrepancy between the produced power and the load. If we go back to the df.columns command, we see that we missed one crucial part: The Import Balance. The german energy grid is thoroughly connected with its neighbouring countries, so a significant amount of energy gets transferred at every timestep. We redesign the violin plot to account for the import/export balance:


In [ ]:
# we create the new column
data_df['Energy_Balance_Final'] = data_df['Energy_Balance'] + data_df["Import Balance"]

# Create the first violin plot for 'Energy_Balance'
fig = px.violin(data_df, y='Energy_Balance', box=True, points=False, title='Energy Balance Violin Plot')

# Create the second violin plot for 'Energy_Balance_Final' and add it to the first plot
fig.add_trace(px.violin(data_df, y='Energy_Balance_Final', box=True, points=False, title='Energy Balance Final Violin Plot').data[0])

# Update the layout to show subplots side by side
fig.update_layout(violingap=0)  # You can adjust the gap between the subplots as needed

# Add annotations for each violin plot title
fig.add_annotation(
    go.layout.Annotation(
        text="Energy Balance (Original)",
        xref="paper",
        yref="paper",
        x=0.15,  # x-coordinate position of the title
        y=1,    # y-coordinate position of the title
        showarrow=False,
        font=dict(size=16, color="black"),
    )
)

fig.add_annotation(
    go.layout.Annotation(
        text="Energy Balance (with Imports)",
        xref="paper",
        yref="paper",
        x=0.85,  # x-coordinate position of the title
        y=1, # y-coordinate position of the title
        showarrow=False,
        font=dict(size=16, color="black"),
    )
)

# update the y axis label
fig.update_yaxes(title_text="Energy Balance [MW]")

# Show the combined plot
fig.show()



# Yearly and monthly summary of power production

In this chapter, we will plot the different energy sources. To make the plots readable and keep the different energy sources distinguishable, we need a dictionary mapping the energy sources to their respective colors.
We ask a LLM to create a dictionary for us.

In [ ]:
# Create a dictionary to map energy sources to colors
colors = {
    'Import Balance': 'lightgray',
    'Nuclear': 'red',
    'Hydro Run-of-River': 'blue',
    'Biomass': 'green',
    'Fossil brown coal / lignite': 'brown',
    'Fossil hard coal': 'black',
    'Fossil oil': 'orange',
    'Fossil gas': 'purple',
    'Geothermal': 'gray',
    'Hydro water reservoir': 'cyan',
    'Hydro pumped storage': 'magenta',
    'Others': 'yellow',
    'Waste': 'pink',
    'Wind offshore': 'darkblue',
    'Wind onshore': 'darkgreen',
    'Solar': 'gold',
    'Load': 'darkred'
}

For some function calls, we need the nex notation of the colors, so we [ask our favourite LLM](https://chat.openai.com/share/94ac63f4-ff61-41e3-8e03-4db78ac7c0c6) to map them for us:

In [ ]:
colors_hex = {
    'Import Balance': '#D3D3D3',  # lightgray
    'Nuclear': '#FF0000',         # red
    'Hydro Run-of-River': '#0000FF',  # blue
    'Biomass': '#00FF00',         # green
    'Fossil brown coal / lignite': '#A52A2A',  # brown
    'Fossil hard coal': '#000000',  # black
    'Fossil oil': '#FFA500',      # orange
    'Fossil gas': '#800080',      # purple
    'Geothermal': '#808080',      # gray
    'Hydro water reservoir': '#00FFFF',  # cyan
    'Hydro pumped storage': '#FF00FF',   # magenta
    'Others': '#FFFF00',          # yellow
    'Waste': '#FFC0CB',           # pink
    'Wind offshore': '#00008B',    # darkblue
    'Wind onshore': '#006400',     # darkgreen
    'Solar': '#FFD700',           # gold
    'Load': '#8B0000'             # darkred
}

Next we want to create a pie chart, to check the fractions of the total power generation that are generated by each power source.

In [ ]:
# this creates a subset of the data_df containing only the columns with the power sources, and the takes the sum of each column, returning a simple Pandas Series
sum_of_power_sources = data_df[power_sources].sum()


In [ ]:
# Prepare the data for the pie chart
pie_data = pd.DataFrame({'Power Source': sum_of_power_sources.index, 'Total Power': sum_of_power_sources.values})

# Create the pie chart
fig = px.pie(pie_data, values='Total Power', names='Power Source', color='Power Source',
             color_discrete_map=colors, title='Sum of Power Sources', hole=0.3)

# Show the plot
fig.show()


another interesting thing will be to see how the distribution changes for different months of the year. For this we need to group the dataframe by month, and plot one pie chart for each month:



In [ ]:
# Group data by 'month'
grouped_data = data_df.groupby('month').sum()

# Create a pie chart for each month
for month in grouped_data.index:
    sum_of_power_sources = grouped_data.loc[month, power_sources]
    pie_data = pd.DataFrame({'Power Source': sum_of_power_sources.index, 'Total Power': sum_of_power_sources.values})

    fig = px.pie(pie_data, values='Total Power', names='Power Source', color='Power Source',
                 color_discrete_map=colors, title=f'Energy source contribution for {month_number_to_name[month]}', hole=0.3)

    fig.show()

<ipython-input-15-9f1faecba7ce>:2: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.



Another way to visualize the data is with a box/violin plot for each resource:

This plot was partly created with the help of LLMs, see [here](https://chat.openai.com/share/57f0cd0f-be4c-4132-b2b6-959adc1c117c)


In [ ]:
# Box plot for each power resource

for power_source in power_sources: # loop through all columns
    # print(colors_hex[power_source])
    fig = px.box(data_df, y=power_source, title=f'Distribution of {power_source}',
                 labels={'value': 'Power Value'}, color_discrete_sequence=["grey"])

    # Create violin plot
    fig.add_trace(px.violin(data_df, y=power_source, box=False, color_discrete_sequence=[colors_hex[power_source]]).data[0])

    fig.show()

If we use GraphObjects (go) from plotly instead of PlotlyExpress, we need to manually set the colour for both filling and frame of the Violin plot, so we ask an LLM to write us a function converting a hex code of a colour into the hex code of its equivalent with a 50% opacity.

In [ ]:
def hex_to_50_opacity(hex_color):
    # Remove the '#' symbol if present
    hex_color = hex_color.lstrip('#')

    # Get the RGB components from the hex string
    r = int(hex_color[0:2], 16)
    g = int(hex_color[2:4], 16)
    b = int(hex_color[4:6], 16)

    # Calculate the 50% opacity
    r_50_opacity = int((r + 255) / 2)
    g_50_opacity = int((g + 255) / 2)
    b_50_opacity = int((b + 255) / 2)

    # Convert the RGB components to hex and combine to get the final color
    color_50_opacity = f'#{r_50_opacity:02x}{g_50_opacity:02x}{b_50_opacity:02x}'

    return color_50_opacity

Now, we compare the difference between the histogram of a power source and its violin plot. Note how changing spanmode from soft (which is default) to hard changes the shape of the violin plot.

In [ ]:
for power_source in power_sources:
    # Create a subplot with 2 rows and 1 column
    fig = make_subplots(rows=1, cols=2, shared_yaxes=True, horizontal_spacing=0.05)

    # Create the violin plot in the left subplot. See how different spanmodes affect the outcome.
    # fig.add_trace(go.Violin(y=data_df[power_source], box_visible=True, fillcolor=hex_to_50_opacity(colors_hex[power_source]), line_color=colors_hex[power_source], spanmode='soft'), row=1, col=1)
    fig.add_trace(go.Violin(y=data_df[power_source], box_visible=True, fillcolor=hex_to_50_opacity(colors_hex[power_source]), line_color=colors_hex[power_source], spanmode='hard'), row=1, col=1)
    fig.update_yaxes(title_text=power_source, row=1, col=1)
    fig.update_yaxes(row=1, col=2)
    fig.update_xaxes(showticklabels=False, row=1, col=1)

    # Create the histogram in the right subplot
    fig.add_trace(go.Histogram(y=data_df[power_source], nbinsx=50, marker_color=colors_hex[power_source]), row=1, col=2)

    # Update the layout
    fig.update_layout(height=600, width=1000, title_text="Violin plot vs Histogram for " + power_source, showlegend=False)

    # Show the plot
    fig.show()

What we notice is that the violin plot extends further than the maximum and minimum points for each data series. This happens because by default, the 'spanmode' attribute of the Violin Graph object is set to 'soft'. So probabilities are also computed for values outside of the current range of the data. While this behaviour is desirable in some cases (like the maximum power), it is undesirable in others (like when it leads to negative power consumption).
Like always, which plot is the most representative depends on the circumstances and the data we are plotting.


# Load analysis

We took a look at the supply side, the next step is to get an overview over the load distribution.
We make a series of box plots to understand the load distribution:

[LLM link](https://chat.openai.com/share/726532b7-105b-4453-8d8f-f38eb7d5e0f9)


In [ ]:
# Create the box plot using Plotly Express
fig = px.box(data_df, x='hour_of_day', y='Load', points="outliers")

# Update the layout of the figure for better visualization
fig.update_layout(
    title="Box Plot of Loads for Each Hour of the Day",
    xaxis_title="Hour of the Day",
    yaxis_title="Load [MW]",
    xaxis=dict(tickvals=list(range(0, 24)), ticktext=[f"{h}:00" for h in range(0, 24)]),
)

# Show the plot
fig.show()

We can see that there is a strong diurnal trend in the Load on the system, but also a significant spread for each individual hour. One thing to investigate is how much the daily load is likely to move within the box plot quantiles for a given day. To investigate that, we draw a point cloud for the entire year that we can shift through, and plot the diurnal load for a random subset of the data.

In [ ]:
data_df['day'] = data_df['Date (GMT+1)'].apply(lambda x: x.timetuple().tm_yday)

In [ ]:
fig_point_cloud = px.scatter(data_df, x="hour_of_day", y="Load",
                            title="Load Distribution by Hour of Day",
                            animation_frame="day",  # To create a separate frame for each day
                            animation_group="hour_of_day",  # Points with the same hour will be connected
                            range_x=[1, 24],  # Specify the range of x-axis (hour_of_day)
                            range_y=[data_df["Load"].min(), data_df["Load"].max()],  # Specify the range of y-axis (Load)
                            labels={"Load": "Load [MW]"})

# Step 2: Draw a random sample of 30 days and create line plots for those 30 days
random_sample_days = sorted(random.sample(range(1, 366), 20))

# Filter the DataFrame to get data for the random sample days
sample_data_df = data_df[data_df["day"].isin(random_sample_days)]

# Get the first entry of the sample data for each day
first_entry_of_sample_data = sample_data_df.groupby("day").first()

# Create a dictionary to map each unique month to a random color
months = sorted(data_df["month"].unique())
month_to_color = {month: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] for i, month in enumerate(months)}

# Create the line plot for the random sample days
fig_line_plot = go.Figure()

for day in random_sample_days:
    day_data = sample_data_df[sample_data_df["day"] == day]
    month_color = month_to_color[first_entry_of_sample_data.loc[day, "month"]]
    fig_line_plot.add_trace(go.Scatter(x=day_data["hour_of_day"], y=day_data["Load"],
                                       mode="lines", line=dict(color=month_color),
                                       name=f"Day {day}", showlegend=True))

fig_line_plot.update_layout(title="Load Profile for 30 Random Days",
                            xaxis_title="Hour of Day",
                            yaxis_title="Load (Units)",)

# Display the plots
fig_point_cloud.show()
fig_line_plot.show()


Another way to visulize the load over time is with a heatmap (also called carpet plot). Here we draw a grid of hours of the day vs. days of the year, and color code the load for each hour. The plot below is shown both for an entire year, and for a sample month.

In [ ]:
# Create the heatmap using Plotly
fig = go.Figure(go.Heatmap(
    z=data_df['Load'],
    x=data_df['day'],
    y=data_df['hour_of_day'],
    colorscale='Viridis',  # You can choose any other colorscale
))

# Customize the plot layout
fig.update_layout(
    title="Heatmap of Load vs. Day and Hour",
    xaxis=dict(title="Day"),
    yaxis=dict(title="Hour of Day"),
)

# Show the plot
fig.show()

# define a month number:
month_number = 4

# Extract the entries in the month of March
data_df_short = data_df[pd.to_datetime(data_df['Date (GMT+1)'], utc=True).dt.month == month_number]

# Create the heatmap using Plotly and retain the mapping of values to colors
fig = go.Figure(go.Heatmap(
    z=data_df_short['Load'],
    x=data_df_short['day'],
    y=data_df_short['hour_of_day'],
    colorscale='Viridis',  # You can choose any other colorscale
    zmin=data_df['Load'].min(),  # Set the zmin to the same value as in the first heatmap
    zmax=data_df['Load'].max(),  # Set the zmax to the same value as in the first heatmap
))

# Customize the plot layout
fig.update_layout(
    title="Heatmap of Load over time in month: " + str(month_number),
    xaxis=dict(title="Day"),
    yaxis=dict(title="Hour of Day"),
)

# Show the plot
fig.show()

we can also show this information in a 3d plot for a given month:


In [ ]:

subset_data_df = data_df[data_df.month == 4]
from scipy.interpolate import griddata
# fig = px.scatter_3d(subset_data_df, x='hour_of_day', y='day', z='Load', color='Load', size_max=10)

hour_of_day_grid, day_grid = np.meshgrid(np.linspace(subset_data_df['hour_of_day'].min(), subset_data_df['hour_of_day'].max(), 50),
                                         np.linspace(subset_data_df['day'].min(), subset_data_df['day'].max(), 50))

# Perform interpolation to get the 'Load' values on the grid
load_grid = griddata((subset_data_df['hour_of_day'], subset_data_df['day']), subset_data_df['Load'], (hour_of_day_grid, day_grid), method='linear')

# Create the 3D surface plot
fig = go.Figure(data=[go.Surface(z=load_grid, x=hour_of_day_grid, y=day_grid)])

# Set the axis labels:
fig.update_layout(scene=dict(xaxis_title='hour_of_day', yaxis_title='day', zaxis_title='Load'))

# Adjust the size of the plot
fig.update_layout(width=800, height=800)

fig.show()

# Power price analysis


The same heatmap and plot can also be drawn for the power price.

In [ ]:
# Create the heatmap using Plotly
fig = go.Figure(go.Heatmap(
    z=data_df['Day Ahead Auction'],
    x=data_df['day'],
    y=data_df['hour_of_day'],
    colorscale='Viridis',  # You can choose any other colorscale
))

# Customize the plot layout
fig.update_layout(
    title="Heatmap of Price vs. Day and Hour",
    xaxis=dict(title="Day"),
    yaxis=dict(title="Hour of Day"),
)

# Show the plot
fig.show()

# define a month number:
month_number = 4

# Extract the entries in the month of the month_number
data_df_short = data_df[pd.to_datetime(data_df['Date (GMT+1)'], utc=True).dt.month == month_number]

# Create the heatmap using Plotly and retain the mapping of values to colors
fig = go.Figure(go.Heatmap(
    z=data_df_short['Day Ahead Auction'],
    x=data_df_short['day'],
    y=data_df_short['hour_of_day'],
    colorscale='Viridis',  # You can choose any other colorscale
    zmin=data_df['Day Ahead Auction'].min(),  # Set the zmin to the same value as in the first heatmap
    zmax=data_df['Day Ahead Auction'].max(),  # Set the zmax to the same value as in the first heatmap
))

# Customize the plot layout
fig.update_layout(
    title="Price over time for month Nr: " + str(month_number),
    xaxis=dict(title="Day"),
    yaxis=dict(title="Hour of Day"),
)

# Show the plot
fig.show()

In [ ]:

subset_data_df = data_df[data_df.month == 4]
# fig = px.scatter_3d(subset_data_df, x='hour_of_day', y='day', z='Load', color='Load', size_max=10)

hour_of_day_grid, day_grid = np.meshgrid(np.linspace(subset_data_df['hour_of_day'].min(), subset_data_df['hour_of_day'].max(), 50),
                                         np.linspace(subset_data_df['day'].min(), subset_data_df['day'].max(), 50))

# Perform interpolation to get the 'Load' values on the grid
load_grid = griddata((subset_data_df['hour_of_day'], subset_data_df['day']), subset_data_df['Day Ahead Auction'], (hour_of_day_grid, day_grid), method='linear')



# Create the 3D surface plot with the stretched z-values
fig = go.Figure(data=[go.Surface(z=load_grid, x=hour_of_day_grid, y=day_grid)])

# Set the axis labels
fig.update_layout(scene=dict(xaxis_title='hour_of_day', yaxis_title='day', zaxis_title='Price'))

# Adjust the size of the plot
fig.update_layout(width=800, height=800)

fig.show()

# Create the 3D surface plot
#fig = go.Figure(data=[go.Surface(z=load_grid, x=hour_of_day_grid, y=day_grid)])

# Set the axis labels:
#fig.update_layout(scene=dict(xaxis_title='hour_of_day', yaxis_title='day', zaxis_title='Price'))

# Adjust the size of the plot
#fig.update_layout(width=800, height=800)

#fig.show()

# Power generation time series

now we generate a subset of the data that is only in a certain week, and generate the plot. feel free to cange the plot_week variable, and observe how the plot below changes


In [ ]:
# make a list of the weeks we want to plot
weeks_to_plot = range(0, 52, 5)

In [ ]:

# energy_sources = list_of_columns.drop(['Date (GMT+1)', 'Day Ahead Auction', 'hour_of_day', 'month'])
for week in weeks_to_plot:

  data_subset = data_df.iloc[week * 24 * 7: week * 24 * 7 + 24 * 7]

  # Calculate the cumulative sum for each column except 'Load'
  data_cumulative = data_subset.drop(['Load', 'Date (GMT+1)', 'Day Ahead Auction', 'hour_of_day', 'month'], axis=1).apply(pd.to_numeric, errors='coerce').cumsum(axis=1)


  # Convert non-numeric values to NaN
  data_subset = data_subset.apply(pd.to_numeric, errors='coerce')


  # Create a trace for each column
  traces = []
  for column in data_cumulative.columns:
      # Exclude 'Load' and 'Import Balance' from the stacked area chart
      if column in power_sources:
          trace = go.Scatter(
              x=data_subset.index,
              y=data_cumulative[column],
              mode='lines',
              name=column,
              fill='tonexty',
              fillcolor=colors[column],
              line=dict(color=colors[column])
          )
          traces.append(trace)

  fig = go.Figure(data=traces)

  # Add 'Import Balance' as a separate trace at the bottom
  import_balance_trace = go.Scatter(
      x=data_subset.index,
      y=data_subset['Import Balance'],
      mode='lines',
      name='Import Balance',
      fill='tozeroy',
      fillcolor=colors['Import Balance'],
      line=dict(color=colors['Import Balance'])
  )
  fig.add_trace(import_balance_trace)

  # Update layout properties
  fig.update_layout(
      title='Stacked Line Chart Week ' + str(week),
      xaxis=dict(title='hour_of_year'),
      yaxis=dict(title='Power [MW]'),
      showlegend=True
  )

  # Show the plot
  # fig.write_image('stacked_line_chart.png')
  fig.show()



To get a more aggregate view of power production in different times of the year, we can split the series into chunks of varying length, and check how they differ throughout the year. A good way to display this information is in a bubble plot.


In [ ]:
# first we group the information by the relevant days_to_group (choose anything between 1 and 60)
fractions_solar = []
fractions_wind = []
total_productions = []
group_names = []

days_to_group = 14  # 1-30
for group_start in range(0, 365, days_to_group):
    days_in_group = list(range(group_start, group_start + days_to_group))
    df_subset = data_df[data_df["day"].isin(days_in_group)]
    total_production = df_subset[power_sources].sum(axis=1).sum()
    total_productions.append(total_production)
    fractions_solar.append(round(df_subset["Solar"].sum() / total_production, 2))
    fractions_wind.append(round((df_subset["Wind onshore"].sum() + df_subset["Wind offshore"].sum()) / total_production, 2))

    group_names.append(int(group_start / days_to_group))

total_hourly = [round(x / 24 / days_to_group / 1000, 2) for x in total_productions]

In [ ]:
# Calculate the sum of x and y values
sum_values = [x + y for x, y in zip(fractions_solar, fractions_wind)]


# Create the scatterplot
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=fractions_solar,
        y=fractions_wind,
        mode="markers",
        marker_size=total_hourly,
        marker=dict(
            color=sum_values,  # Set color based on normalized sum values
            colorscale='RdYlGn',  # Use the RdYlGn color scale
            cmin = 0.1,
            cmax = 0.7,
            colorbar=dict(title="Sum of X and Y"),
        ),
        text=group_names,
        textposition='middle center',  # Show text inside markers  # Hide the legend (table with values)
    )
)

# Add x and y labels
fig.update_layout(
    xaxis_title="Fraction Solar power",
    yaxis_title="Fraction Wind power",
    yaxis_ticks="outside",  # Show y-axis ticks outside the plot
)

fig.show()

# Scatter plots energy production

apart from splitting data into time series, we can also make scatter plots between different series, to explore how they might or might not be correlated. The first scatter plot is between the price and the amount of solar power in the grid.

In [ ]:
# Assuming data_df is your pandas DataFrame
fig = px.scatter(data_df, y='Day Ahead Auction', x='Solar', title='Scatter plot: Solar vs. Day Ahead Auction')

# Show the plot
fig.show()

We can see there is a slight negative correlation between the amount of solar power and the power price (which was expected), but still a lot of noise.

A more sophisticated plot is to plot the correlation between the residual load and the power price, where residual load is all load that is not covered by renewable sources.

In [ ]:
# Calculate the residual load
data_df['Residual Load'] = data_df["Load"] - data_df[renewable_sources].sum(axis=1)  # - data_df['Solar'] - data_df['Wind onshore'] - data_df['Wind offshore']

# Create the scatter plot
fig = px.scatter(data_df, x='Residual Load', y='Day Ahead Auction', title='Scatter plot: Sum of Solar, Wind Onshore, and Wind Offshore vs. Day Ahead Auction')

# Show the plot
fig.show()

We can see that the noise is much less, but still very noticeable, particularly around the extreme cases where the residual load is either negative, or very high (more than 45GW).

# Experimental QQ plots

We can also check if the import balance follows a normal distribution. We follow the steps:

1) sort the column in ascending order
2) calculate the quantiles for the theory
3) calculate the quantiles for the column
4) create a plotly scatter


In [ ]:
import scipy.stats as stats
data_df.sort_values(by='Import Balance', inplace=True)

In [ ]:
n = data_df.shape[0]
theoretical_quantiles = stats.norm.ppf([(i - 0.5) / n for i in range(1, n + 1)])
observed_quantiles = data_df['Import Balance'].values

In [ ]:

# Sort the 'Import Balance' column in ascending order
data_df.sort_values(by='Import Balance', inplace=True)

# Estimate mean (mu) and standard deviation (sigma) from the data
mu = data_df['Import Balance'].mean()
sigma = data_df['Import Balance'].std()

# Calculate the theoretical quantiles based on the number of data points
n = data_df.shape[0]
theoretical_quantiles = stats.norm.ppf([(i - 0.5) / n for i in range(1, n + 1)], loc=mu, scale=sigma)

# Calculate the quantiles for the 'Import Balance' column
observed_quantiles = data_df['Import Balance'].values

# Create a Plotly scatter plot for the Q-Q plot with the fitted normal distribution
fig = go.Figure()

fig.add_trace(go.Scatter(x=theoretical_quantiles,
                         y=observed_quantiles,
                         mode='markers',
                         marker=dict(size=5),
                         line=dict(color='blue'),
                         name='Q-Q Plot'))

# Add the fitted normal distribution line
fig.add_trace(go.Scatter(x=theoretical_quantiles,
                         y=theoretical_quantiles,
                         mode='lines',
                         line=dict(color='red', dash='dash'),
                         name='Fitted Normal Distribution'))

fig.update_layout(title='Q-Q Plot with Fitted Normal Distribution',
                  xaxis_title='Theoretical Quantiles',
                  yaxis_title='Observed Quantiles')

fig.show()